In [1]:
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import matplotlib.image as img
import numpy as np
import cv2
import os, shutil
from scipy.spatial import distance
import xml.etree.ElementTree as ET

### Annotation 파일 읽어오기
https://codechacha.com/ko/python-parsing-xml-and-pretty-print/

In [2]:
import os 

path = './total_20220724_20220818_update'
annotation_list = os.listdir(path) 
annotation_list.remove('images')
print(annotation_list)

['annotations45.xml', 'annotations41.xml', 'annotations15.xml', 'annotations25.xml', 'annotations63.xml', 'annotations10.xml', 'annotations65.xml', 'annotations27.xml', 'annotations61.xml', 'annotations17.xml', 'annotations38.xml', 'annotations6.xml', 'annotations58.xml', 'annotations29.xml', 'annotations49.xml', 'annotations35.xml', 'annotations42.xml', 'annotations39.xml', 'annotations31.xml', 'annotations40.xml', 'annotations57.xml', 'annotations22.xml', 'annotations2.xml', 'annotations1.xml', 'annotations55.xml', 'annotations28.xml', 'annotations62.xml', 'annotations3.xml', 'annotations36.xml', 'annotations11.xml', 'annotations60.xml', 'annotations12.xml', 'annotations48.xml', 'annotations30.xml', 'annotations7.xml', 'annotations8.xml', 'annotations26.xml', 'annotations18.xml', 'annotations23.xml', 'annotations64.xml', 'annotations21.xml', 'annotations54.xml', 'annotations19.xml', 'annotations51.xml', 'annotations53.xml', 'annotations59.xml', 'annotations44.xml', 'annotations43.xml

In [25]:
# 각 행의 n 번째 열을 기준으로 sort (오름차순)
# x : nd array
# axis : 기준 열
def sort_ndarray_by_col(x, axis=0):
    size = x.shape[0]
    col = [x[i][axis] for i in range(size)] # 기준 행의 원소들을 추출
    sorted_col = sorted(col) # 추출된 원소들을 정렬
    rank = [sorted_col.index(x[i][axis]) for i in range(size)] # 정렬된 index 추출
    #print(rank)
    try:
        sorted_array = [x[rank.index(i)] for i in range(size)]  # 정렬된 index 순서대로 정렬
    except: # 똑같은 순위가 있는 경우 예외처리
        overlap_rank = []
        for i in range(size):
            if rank.count(i) > 1:
                overlap_rank.append(i)
        for r in overlap_rank:
            overlap_list = [i for i in range(size) if rank[i]==r]
            for k, idx in enumerate(overlap_list):
                rank[idx] += k
        sorted_array = [x[rank.index(i)] for i in range(size)]  # 정렬된 index 순서대로 정렬

    return np.array(sorted_array)

# 함수화
def perspective_transform(src, point, height=256, width=256):    
    # 4 꼭지점 분류 
    sorted_by_y= sort_ndarray_by_col(point, 1)
    top_two = sorted_by_y[0:2]
    topLeft, topRight = sort_ndarray_by_col(top_two, 0)
    bottom_two = sorted_by_y[2:4]
    bottomLeft, bottomRight = sort_ndarray_by_col(bottom_two, 0)
    #print("tl:", topLeft)
    #print("bl", bottomLeft)
    #print("tr", topRight)
    #print("br", bottomRight)
    
    
    # 변환 전 4개 좌표 
    srcPoint = np.float32([topLeft, topRight, bottomRight , bottomLeft])

    # 변환 후 4개 좌표
    dstPoint = np.array([[0, 0], [width, 0], [width, height], [0, height]], dtype=np.float32)

    # Perspective transformation
    matrix = cv2.getPerspectiveTransform(srcPoint, dstPoint)
    dst = cv2.warpPerspective(src, matrix, (width, height))
    
    return dst

# 이미지 상에 polygon 그리기
def draw_label(img_path, points, save_path=""):
    '''
    image = img.imread(img_path)
    plt.imshow(image)

    ax = plt.gca()

    point = np.array([[data['p1'][0], data['p1'][1]],
                      [data['p2'][0], data['p2'][1]],
                      [data['p3'][0], data['p3'][1]],
                      [data['p4'][0], data['p4'][1]]])
    #print(point)

    polygon = patches.Polygon(point, fill=None ,edgecolor='k',ls='solid',lw=3)

    ax.add_patch(polygon)

    plt.show()
    '''
    src = cv2.imread(img_path, cv2.IMREAD_COLOR)
    dst = cv2.polylines(src, np.int32([points]), True, (255, 0, 0), 6)

    return dst

def extract_bb_points(points, width, height):
    if len(points.split(';')) == 5: # 라벨링된 point가 5개인 경우
        ps = [(float(points.split(';')[0].split(',')[0]), float(points.split(';')[0].split(',')[1])),
             (float(points.split(';')[1].split(',')[0]), float(points.split(';')[1].split(',')[1])),
             (float(points.split(';')[2].split(',')[0]), float(points.split(';')[2].split(',')[1])),
             (float(points.split(';')[3].split(',')[0]), float(points.split(';')[3].split(',')[1])),
             (float(points.split(';')[4].split(',')[0]), float(points.split(';')[4].split(',')[1]))]
        left, right, up, down = [], [], [], []
        for i, p in enumerate(ps):
            #print(i,p)
            if p[0] == 0: # 점이 이미지 왼쪽 끝에 존재
                left.append(i)
            if p[0] == float(width): # 점이 이미지 오른쪽 끝에 존재
                right.append(i)
            if p[1] == 0: # 점이 이미지 위쪽 끝에 존재
                up.append(i)
            if p[1] == float(height): # 점이 이미지 아래쪽 끝에 존재
                down.append(i)
        #print(len(left), len(right), len(up), len(down))

        if len(left) == 2: # 이미지 왼쪽 끝에 점이 두 개 있는 경우 하나 제거
            del ps[left[0]]
        elif len(right) == 2: # 이미지 오른쪽 끝에 점이 두 개 있는 경우 하나 제거
            del ps[right[0]]
        elif len(up) == 2: # 이미지 위쪽 끝에 점이 두 개 있는 경우 하나 제거
            del ps[up[0]]
        elif len(down) == 2: # 이미지 아래쪽 끝에 점이 두 개 있는 경우 하나 제거
            del ps[down[0]]
        
        # 4 꼭지점 분류 
        sorted_by_y= sort_ndarray_by_col(np.array(ps), 1)
        top_two = sorted_by_y[0:2]
        topLeft, topRight = sort_ndarray_by_col(top_two, 0)
        bottom_two = sorted_by_y[2:4]
        bottomLeft, bottomRight = list(sort_ndarray_by_col(bottom_two, 0))

    elif len(points.split(';')) == 4: # 라벨링된 point가 4개인 경우 = polygon 라벨링 (없음)
        ps = [(float(points.split(';')[0].split(',')[0]), float(points.split(';')[0].split(',')[1])),
             (float(points.split(';')[1].split(',')[0]), float(points.split(';')[1].split(',')[1])),
             (float(points.split(';')[2].split(',')[0]), float(points.split(';')[2].split(',')[1])),
             (float(points.split(';')[3].split(',')[0]), float(points.split(';')[3].split(',')[1]))]

        # 4 꼭지점 분류 
        sorted_by_y= sort_ndarray_by_col(np.array(ps), 1)
        top_two = sorted_by_y[0:2]
        topLeft, topRight = sort_ndarray_by_col(top_two, 0)
        bottom_two = sorted_by_y[2:4]
        bottomLeft, bottomRight = list(sort_ndarray_by_col(bottom_two, 0))

    elif len(points.split(';')) == 2: # 라벨링된 point가 2개인 경우 = 직선 라벨링 (있음))
        ps = [(float(points.split(';')[0].split(',')[0]), float(points.split(';')[0].split(',')[1])),
             (float(points.split(';')[1].split(',')[0]), float(points.split(';')[1].split(',')[1]))]

        # 2 꼭지점 분류
        if ps[0][0] < ps[1][0]:
            bottomLeft = ps[0]
            bottomRight = ps[1]
        else:
            bottomLeft = ps[1]
            bottomRight = ps[0]
    else:
        return None, 0, None
    
    print(len(points.split(';')))
    print('bb', bottomLeft, bottomRight) # bounding box 생성에 기준이 되는 주차면 앞 라인의 두 점
                    
    # 라인으로부터 바운딩 박스 생성
    x_offset = 0
    width = distance.euclidean(bottomLeft, bottomRight)+x_offset
    y_offset = width/10.0
    height = -width*2/3.0
    #print(ps, width, height)


    b1 = (bottomLeft[0], bottomLeft[1]+y_offset)
    b2 = (bottomRight[0], bottomRight[1]+y_offset)
    b3 = (b2[0], b2[1]+height)
    b4 = (b1[0], b1[1]+height)
    print('ps:',np.array([b1, b2, b3, b4]), width, np.array(ps))
    
    return np.array([b1, b2, b3, b4]), width, np.array(ps)

def get_occupied_info(polyline, width, height):
    label = polyline.get('label')
    points = polyline.get('points') # 2개
    bb_points, width, _ = extract_bb_points(points, width, height)
    return label, width, bb_points

def get_empty_info(polygon, width, height):
    label = polygon.get('label')
    points = polygon.get('points') # 4개 or 5개
    bb_points, width, poly_points = extract_bb_points(points, width, height)
    empty_type_dict = {'일반형':0, '경형':1, '장애인전용':2, '여성우선주차장':3, '환경친화적 자동차 전용':4, 'etc':5, '기타':5}
    empty_type = empty_type_dict[polygon.find('attribute').text]
    return label, width, bb_points, poly_points, empty_type
    
def get_obstacle_info(polygon, width, height):
    label = polygon.get('label')
    points = polygon.get('points')
    bb_point, width, poly_points = extract_bb_points(points, width, height)
    obstacle_type_dict = {'사람':0, '이륜차':1, '기타':2}
    obs_type = obstacle_type_dict[polygon.find('attribute').text]
    return label, width, bb_points, poly_points, obs_type

In [21]:
occupied_cnt, empty_cnt, obstacle_cnt = 0, 0, 0

datasets = {}
datasets['occupied'] = {}
datasets['empty'] = {}
datasets['obstacle'] = {}

for annotation in annotation_list:
    print(annotation)
    # annotation 파일 불러오기
    filePath = os.path.join(path, annotation)
    #print(filePath)
    tree = ET.parse(filePath)
    root = tree.getroot()
    for image in root.findall("image"):
        image_attrib = image.attrib
        image_name = image_attrib.get('name')
        print(image_name)
        image_witdh = image_attrib.get('width')
        image_height = image_attrib.get('height')
        polylines = image.findall('polyline') # 있음 라벨링
        polygons = image.findall('polygon') # 없음 라벨링
        
        for polyline in polylines: # 있음
            polyline_label, width, bb_points = get_occupied_info(polyline, image_witdh, image_height)
            print(polyline_label) 
            if width > 250: # 길이가 너무 짧은 경우 넘어감
                occupied_cnt += 1 
                datasets['occupied'][str(occupied_cnt)]={'label':polyline_label, 'src':image_name,
                                                         'width': width,
                                                         'bb_points':bb_points
                                                        }
            
        for polygon in polygons:
            label = polygon.get('label')
            if label == '없음': # 없음
                empty_label, width, bb_points, poly_points, empty_type = get_empty_info(polygon, image_witdh, image_height)
                print(empty_label, empty_type)
                if (type(bb_points) != None) and (width > 250): # point 정보가 없거나 길이가 너무 짧은 경우 넘어감
                    empty_cnt += 1
                    datasets['empty'][str(empty_cnt)]={'label':empty_label, 'src':image_name, 
                                                       'width': width,
                                                       'type':empty_type,
                                                       'bb_points':bb_points,
                                                       'poly_points':poly_points
                                                      }
                
            elif label == '장애물': # 장애물
                obs_label, width, bb_points, poly_points, obs_type = get_obstacle_info(polygon, image_witdh, image_height)
                print(obs_label, obs_type)
                obstacle_cnt += 1
                datasets['obstacle'][str(obstacle_cnt)]={'label':obs_label, 'src':image_name,
                                                         'width': width,
                                                         'type':obs_type,
                                                         'poly_points':poly_points
                                                        }
                
        #occupied_cnt += len(polylines)
        #empty_cnt += len(polygons)
        #print(image_name, '| 있음', len(polylines), '없음', len(polygons))
    

annotations45.xml
VID_20220724_164941_00_017_2022-08-08_12-45-50_스크린샷.jpg
2
bb (1331.76, 1029.66) (1742.39, 993.45)
ps: [[1331.76       1070.88234358]
 [1742.39       1034.67234358]
 [1742.39        759.85671973]
 [1331.76        796.06671973]] 412.2234357723977 [[1331.76 1029.66]
 [1742.39  993.45]]
있음
2
bb (596.16, 895.43) (847.83, 972.26)
ps: [[596.16       921.74361583]
 [847.83       998.57361583]
 [847.83       823.1495103 ]
 [596.16       746.3195103 ]] 263.1361582907223 [[847.83 972.26]
 [596.16 895.43]]
있음
4
bb [860.2  981.09] [1312.33 1036.72]
ps: [[ 860.2        1026.64394975]
 [1312.33       1082.27394975]
 [1312.33        778.58095141]
 [ 860.2         722.95095141]] 455.53949751915025 [[ 860.2   981.09]
 [1312.33 1036.72]
 [1166.62  753.26]
 [1010.32  748.84]]
없음 0
VID_20220724_164941_00_017_2022-08-08_12-46-01_스크린샷.jpg
2
bb (523.74, 834.5) (677.4, 903.38)
ps: [[523.74       851.33919535]
 [677.4        920.21919535]
 [677.4        807.95789302]
 [523.74       739.0778930

 [2877.31       1195.04526696]] 911.355411241959 [[3788.65 1716.78]
 [2877.31 1711.48]]
있음
2
bb (1794.67, 1808.62) (2896.74, 1775.06)
ps: [[1794.67       1918.87808626]
 [2896.74       1885.31808626]
 [2896.74       1150.26417788]
 [1794.67       1183.82417788]] 1102.5808625674579 [[1794.67 1808.62]
 [2896.74 1775.06]]
있음
2
bb (330.53, 1831.58) (1300.14, 1805.09)
ps: [[ 330.53       1928.57717894]
 [1300.14       1902.08717894]
 [1300.14       1255.43931935]
 [ 330.53       1281.92931935]] 969.9717893835883 [[1300.14 1805.09]
 [ 330.53 1831.58]]
있음
DJI_0012_002.MP4_snapshot_01.51_[2022.08.22_18.23.17].jpg
2
bb (1709.89, 1790.96) (2536.4, 1780.4)
ps: [[1709.89       1873.61774578]
 [2536.4        1863.05774578]
 [2536.4        1312.00610726]
 [1709.89       1322.56610726]] 826.5774577739221 [[1709.89 1790.96]
 [2536.4  1780.4 ]]
있음
4
bb [ 323.46 1780.36] [1582.73 1808.62]
ps: [[ 323.46       1906.31870595]
 [1582.73       1934.57870595]
 [1582.73       1094.85399961]
 [ 323.46       106

4
bb [   0. 1436.] [   0.   1696.75]
ps: [[   0.         1462.075     ]
 [   0.         1722.825     ]
 [   0.         1548.99166667]
 [   0.         1288.24166667]] 260.75 [[1075.84 1266.41]
 [ 713.78 1259.35]
 [   0.   1436.  ]
 [   0.   1696.75]]
없음 0
5
bb [2361.6  1571.95] [2437.54 1665.56]
ps: [[2361.6        1584.00392704]
 [2437.54       1677.61392704]
 [2437.54       1597.25441346]
 [2361.6        1503.64441346]] 120.53927036447496 [[3412.46 1669.09]
 [2525.85 1255.81]
 [2368.66 1250.52]
 [2361.6  1571.95]
 [2437.54 1665.56]]
없음 0
4
bb [  70.9  1693.82] [1107.63 1679.69]
ps: [[  70.9        1797.50262872]
 [1107.63       1783.37262872]
 [1107.63       1092.15510393]
 [  70.9        1106.28510393]] 1036.8262871860454 [[1533.28 1257.58]
 [1139.42 1259.35]
 [  70.9  1693.82]
 [1107.63 1679.69]]
없음 0
5
bb [3497.23 1676.16] [3827.5  1510.14]
ps: [[3497.23       1713.1249717 ]
 [3827.5        1547.1049717 ]
 [3827.5        1300.67182702]
 [3497.23       1466.69182702]] 369.6497170295

 [1607.45       1188.06479595]] 1042.103301261444 [[1607.45 1778.59]
 [2649.48 1766.23]]
있음
2
bb (2730.72, 1845.71) (3709.17, 1815.68)
ps: [[2730.72       1943.60107229]
 [3709.17       1913.57107229]
 [3709.17       1260.96392369]
 [2730.72       1290.99392369]] 978.9107228956074 [[2730.72 1845.71]
 [3709.17 1815.68]]
있음
2
bb (42.65, 1773.3) (1067.01, 1760.93)
ps: [[  42.65       1875.74346863]
 [1067.01       1863.37346863]
 [1067.01       1180.4170111 ]
 [  42.65       1192.7870111 ]] 1024.4346863026456 [[1067.01 1760.93]
 [  42.65 1773.3 ]]
있음
DJI_0011_001.MP4_snapshot_00.23_[2022.08.22_18.10.07].jpg
4
bb [ 372.9 1928.7] [1722.25 1896.93]
ps: [[ 372.9        2063.67239553]
 [1722.25       2031.90239553]
 [1722.25       1132.08642535]
 [ 372.9        1163.85642535]] 1349.7239552590004 [[1755.81 1317.63]
 [1722.25 1896.93]
 [ 372.9  1928.7 ]
 [1310.74 1319.39]]
없음 0
4
bb [2216.8 1872.2] [3280.   1847.47]
ps: [[2216.8        1978.54875706]
 [3280.         1953.81875706]
 [3280.       

DJI_0001_001.MP4_snapshot_00.57_[2022.08.22_10.15.33].jpg
2
bb (1351.36, 1715.01) (2283.89, 1716.78)
ps: [[1351.36       1808.26316798]
 [2283.89       1810.03316798]
 [2283.89       1188.34538146]
 [1351.36       1186.57538146]] 932.5316797835878 [[1351.36 1715.01]
 [2283.89 1716.78]]
있음
2
bb (198.07, 1709.71) (1231.26, 1697.35)
ps: [[ 198.07       1813.03639284]
 [1231.26       1800.67639284]
 [1231.26       1111.83377392]
 [ 198.07       1124.19377392]] 1033.2639283842248 [[ 198.07 1709.71]
 [1231.26 1697.35]]
있음
DJI_0001_001.MP4_snapshot_00.58_[2022.08.22_10.15.41].jpg
2
bb (1308.97, 1665.56) (2197.35, 1635.54)
ps: [[1308.97       1754.44870709]
 [2197.35       1724.42870709]
 [2197.35       1131.83732649]
 [1308.97       1161.85732649]] 888.8870708925853 [[1308.97 1665.56]
 [2197.35 1635.54]]
있음
2
bb (2285.65, 1697.35) (3179.33, 1658.5)
ps: [[2285.65       1786.80240438]
 [3179.33       1747.95240438]
 [3179.33       1151.60304186]
 [2285.65       1190.45304186]] 894.5240437797073

...

VID_20220810_154717_00_007_2022-08-16_16-01-09_스크린샷.jpg
2
bb (961.11, 880.15) (1327.77, 856.84)
ps: [[ 961.11        916.89002065]
 [1327.77        893.58002065]
 [1327.77        648.64654968]
 [ 961.11        671.95654968]] 367.4002064506769 [[ 961.11  880.15]
 [1327.77  856.84]]
있음
2
bb (1347.9, 855.78) (1663.69, 822.93)
ps: [[1347.9         887.52940103]
 [1663.69        854.67940103]
 [1663.69        643.01672748]
 [1347.9         675.86672748]] 317.494010337203 [[1347.9   855.78]
 [1663.69  822.93]]
있음
2
bb (434.45, 845.18) (822.29, 845.18)
ps: [[434.45  883.964]
 [822.29  883.964]
 [822.29  625.404]
 [434.45  625.404]] 387.84 [[822.29 845.18]
 [434.45 845.18]]
있음
2
bb (16.93, 866.38) (380.4, 879.09)
ps: [[ 16.93       902.74921569]
 [380.4        915.45921569]
 [380.4        672.99777775]
 [ 16.93       660.28777775]] 363.6921569129584 [[380.4  879.09]
 [ 16.93 866.38]]
있음
VID_20220810_154717_00_007_2022-08-16_16-01-27_스크린샷.jpg
2
bb (1340.59, 947.53) (1861.6, 985.5)
ps: [[1340.59

DJI_0007_001.MP4_snapshot_00.32_[2022.08.22_12.41.30].jpg
2
bb (2239.73, 1843.94) (3431.89, 1911.05)
ps: [[2239.73       1963.34474102]
 [3431.89       2030.45474102]
 [3431.89       1234.42313424]
 [2239.73       1167.31313424]] 1194.0474101558948 [[2239.73 1843.94]
 [3431.89 1911.05]]
있음
2
bb (115.06, 1718.54) (862.14, 1798.02)
ps: [[ 115.06       1793.66959449]
 [ 862.14       1873.14959449]
 [ 862.14       1372.28563123]
 [ 115.06       1292.80563123]] 751.2959448845706 [[ 862.14 1798.02]
 [ 115.06 1718.54]]
있음
4
bb [1097.04 1760.93] [2162.02 1851.01]
ps: [[1097.04       1867.80828623]
 [2162.02       1957.88828623]
 [2162.02       1245.36637802]
 [1097.04       1155.28637802]] 1068.7828623251778 [[1699.29 1268.18]
 [2132.   1273.48]
 [2162.02 1851.01]
 [1097.04 1760.93]]
없음 0
DJI_0007_001.MP4_snapshot_00.32_[2022.08.22_12.41.36].jpg
2
bb (496.55, 1817.45) (1441.44, 1829.81)
ps: [[ 496.55       1911.94708364]
 [1441.44       1924.30708364]
 [1441.44       1294.32652602]
 [ 496.55  

ps: [[1400.81       1974.1110196 ]
 [2773.11       1979.4010196 ]
 [2773.11       1064.52755559]
 [1400.81       1059.23755559]] 1372.310196019836 [[1400.81 1836.88]
 [2773.11 1842.17]]
있음
2
bb (56.78, 1826.28) (1308.97, 1829.81)
ps: [[  56.78       1951.49949756]
 [1308.97       1955.02949756]
 [1308.97       1120.23284714]
 [  56.78       1116.70284714]] 1252.1949756327886 [[  56.78 1826.28]
 [1308.97 1829.81]]
있음
2
bb (2792.54, 1584.32) (3840.0, 1568.74)
ps: [[2792.54       1689.07758626]
 [3840.         1673.49758626]
 [3840.          975.11367783]
 [2792.54        990.69367783]] 1047.5758626467107 [[2792.54 1584.32]
 [3840.   1568.74]]
있음
DJI_0008_001.MP4_snapshot_02.58_[2022.08.18_15.01.44].jpg
2
bb (1416.71, 1766.23) (2755.45, 1720.31)
ps: [[1416.71       1900.18273174]
 [2755.45       1854.26273174]
 [2755.45        961.24452015]
 [1416.71       1007.16452015]] 1339.52731737729 [[2755.45 1720.31]
 [1416.71 1766.23]]
있음
2
bb (2679.51, 1559.59) (3786.88, 1545.46)
ps: [[2679.51   

 [2582.37       1167.47105728]] 900.792251853889 [[2582.37 1677.92]
 [3483.1  1667.33]]
있음
2
bb (530.1, 1695.58) (1533.28, 1686.75)
ps: [[ 530.1        1795.90188601]
 [1533.28       1787.07188601]
 [1533.28       1118.2593126 ]
 [ 530.1        1127.0893126 ]] 1003.2188601197646 [[1533.28 1686.75]
 [ 530.1  1695.58]]
있음
DJI_0004_001.MP4_snapshot_02.15_[2022.08.22_11.48.48].jpg
2
bb (1777.0, 1706.18) (2773.11, 1699.12)
ps: [[1777.         1805.79350188]
 [2773.11       1798.73350188]
 [2773.11       1134.64348934]
 [1777.         1141.70348934]] 996.1350188102014 [[1777.   1706.18]
 [2773.11 1699.12]]
있음
2
bb (2789.01, 1601.98) (3523.73, 1579.02)
ps: [[2789.01       1675.48786625]
 [3523.73       1652.52786625]
 [3523.73       1162.47542461]
 [2789.01       1185.43542461]] 735.0786624572909 [[2789.01 1601.98]
 [3523.73 1579.02]]
있음
2
bb (374.68, 1722.08) (1372.56, 1699.12)
ps: [[ 374.68       1821.89441058]
 [1372.56       1798.93441058]
 [1372.56       1133.5050067 ]
 [ 374.68       11

4
bb [1425.54 1261.11] [1810.56 1261.11]
ps: [[1425.54  1299.612]
 [1810.56  1299.612]
 [1810.56  1042.932]
 [1425.54  1042.932]] 385.02 [[1425.54 1261.11]
 [1600.39 1146.31]
 [1837.05 1141.01]
 [1810.56 1261.11]]
없음 0
4
bb [ 710.25 1711.48] [1694.   1693.82]
ps: [[ 710.25       1809.87085009]
 [1694.         1792.21085009]
 [1694.         1136.2718495 ]
 [ 710.25       1153.9318495 ]] 983.9085008780033 [[1413.18 1257.58]
 [1814.09 1262.88]
 [1694.   1693.82]
 [ 710.25 1711.48]]
없음 0
DJI_0004_003.MP4_snapshot_02.58_[2022.08.22_12.01.32].jpg
2
bb (478.88, 1662.03) (1301.91, 1653.2)
ps: [[ 478.88       1744.33773656]
 [1301.91       1735.50773656]
 [1301.91       1186.78949281]
 [ 478.88       1195.61949281]] 823.0773656224547 [[1301.91 1653.2 ]
 [ 478.88 1662.03]]
있음
2
bb (2617.69, 1697.35) (3582.01, 1679.69)
ps: [[2617.69       1793.7981694 ]
 [3582.01       1776.1381694 ]
 [3582.01       1133.15037342]
 [2617.69       1150.81037342]] 964.4816939683201 [[2617.69 1697.35]
 [3582.01 1679

In [5]:
datasets

{'occupied': {'1': {'label': '있음',
   'src': 'VID_20220724_164941_00_017_2022-08-08_12-45-50_스크린샷.jpg',
   'width': 412.2234357723977,
   'bb_points': array([[1331.76      , 1070.88234358],
          [1742.39      , 1034.67234358],
          [1742.39      ,  759.85671973],
          [1331.76      ,  796.06671973]])},
  '2': {'label': '있음',
   'src': 'VID_20220724_164941_00_017_2022-08-08_12-45-50_스크린샷.jpg',
   'width': 263.1361582907223,
   'bb_points': array([[596.16      , 921.74361583],
          [847.83      , 998.57361583],
          [847.83      , 823.1495103 ],
          [596.16      , 746.3195103 ]])},
  '3': {'label': '있음',
   'src': 'VID_20220724_164941_00_017_2022-08-08_12-46-01_스크린샷.jpg',
   'width': 335.04034637637295,
   'bb_points': array([[ 686.23      ,  951.01403464],
          [1007.67      , 1045.50403464],
          [1007.67      ,  822.14380372],
          [ 686.23      ,  727.65380372]])},
  '4': {'label': '있음',
   'src': 'VID_20220724_164941_00_017_2022-08-08_12

In [6]:
len(datasets['occupied']), len(datasets['empty']), len(datasets['obstacle'])

(7568, 4628, 348)

In [7]:
len(datasets['occupied']) + len(datasets['empty']) + len(datasets['obstacle'])

12544

In [30]:
dataset_name = 'total_20220724_20220818_update'

FOLDER_NAME = dataset_name + '_generated'
DATASET_ROOT = "/root/share/datasets/"
DATASET_PATH = DATASET_ROOT + FOLDER_NAME
EMPTY_PATH = os.path.join(DATASET_PATH, 'Empty') # 없음 patch 저장 폴더
OCCUPIED_PATH = os.path.join(DATASET_PATH, 'Occupied') # 있음 patch 저장 폴더
EMPTY_TYPE_PATH = os.path.join(DATASET_PATH, 'EmptyType')
OBSTACLE_PATH = os.path.join(DATASET_PATH, 'Obstacle')
LABEL_PATH = os.path.join(DATASET_PATH, 'Label')

# 기존 폴더 삭제
if os.path.exists(DATASET_PATH):
    shutil.rmtree(DATASET_PATH)

# 폴더가 없는 경우 생성
if not os.path.isdir(DATASET_PATH):
    os.makedirs(DATASET_PATH)
if not os.path.isdir(EMPTY_PATH):
    os.makedirs(EMPTY_PATH)
if not os.path.isdir(OCCUPIED_PATH):
    os.makedirs(OCCUPIED_PATH)
if not os.path.isdir(EMPTY_TYPE_PATH):
    os.makedirs(EMPTY_TYPE_PATH)
if not os.path.isdir(OBSTACLE_PATH):
    os.makedirs(OBSTACLE_PATH)
if not os.path.isdir(LABEL_PATH):
    os.makedirs(LABEL_PATH)
    
# Open label txt file 
label_file_all = open(DATASET_PATH + '/'+ dataset_name + '_all.txt', 'w')
label_file_occupied = open(DATASET_PATH + '/' + dataset_name + '_occupied.txt', 'w')
label_file_empty = open(DATASET_PATH + '/' + dataset_name + '_empty.txt', 'w')
label_file_empty_type = open(DATASET_PATH + '/' + dataset_name + '_empty_type.txt', 'w')
label_file_obstacle = open(DATASET_PATH + '/' + dataset_name + '_obstacle.txt', 'w')
label_file_total = open(DATASET_PATH + '/' + dataset_name + '_total.txt', 'w')

In [31]:
def define_img_path(dataset_name, path, key, verbose=False):
    path = data['src']
    img_path = os.path.join(dataset_name, 'images', path)
    image_name = category+key+'_'+path.split('.')[0]
    label_img_name = image_name+'_label.jpg'
    label_img_path = os.path.join(LABEL_PATH, label_img_name)
    patch_name = image_name+'.jpg'
    patch_path = os.path.join(PATCH_PATH, patch_name)

    if verbose:
        print(img_path)
        print('image size: %d bytes'%os.path.getsize(img_path))
        print(label_img_name)
        print(label_img_path)
        print(patch_name)
        print(patch_path)

    if data['label'] == '없음':
        empty_type_img_name = 'Empty_type_'+str(data['type'])+'_'+patch_name
        empty_type_img_path = os.path.join(EMPTY_TYPE_PATH, empty_type_img_name)
        return img_path, label_img_path, patch_path, empty_type_img_path
    elif data['label'] == '장애물':
        obstacle_img_name = 'Obstacle_type_'+str(data['type'])+'_'+patch_name
        obstacle_img_path = os.path.join(OBSTACLE_PATH, obstacle_img_name)
        return img_path, label_img_path, obstacle_img_path
    else: 
        return img_path, label_img_path, patch_path

### Generate occupied patches

In [34]:
cnt = 0
category = 'occupied'
PATCH_PATH = OCCUPIED_PATH

# 기존 txt 목록 불러오기
label_file_all_lines = list(open(DATASET_PATH + '/'+ dataset_name + '_all.txt', 'r').readlines()) if os.path.exists(DATASET_PATH + '/'+ dataset_name + '_all.txt') else []
label_file_occupied_lines = list(open(DATASET_PATH + '/' + dataset_name + '_occupied.txt', 'r').readlines()) if os.path.exists(DATASET_PATH + '/'+ dataset_name + '_occupied.txt') else []

for key in datasets[category].keys():
    print(key)
    dataset = datasets[category]
    data = dataset[key] # label src b1 b2 b3 b4
    bb_points = data['bb_points']
    
    img_path, label_img_path, patch_path = define_img_path(dataset_name, data, key)
    
    # check existing file
    if os.path.exists(label_img_path):
        print('label image {} exists'.format(label_img_path.split('/')[-1]))
    if os.path.exists(patch_path):
        print('patch image {} exists'.format(patch_path.split('/')[-1]))
        
    if not os.path.exists(label_img_path) and not os.path.exists(patch_path): # label 이미지와 patch가 없는 경우에만
        # source image
        src = cv2.imread(img_path, cv2.IMREAD_COLOR)

        # labeled image
        label_img = draw_label(img_path, bb_points)

        # save labeled image
        cv2.imwrite(label_img_path, label_img)

        # cropped patch
        patch_img = perspective_transform(src, bb_points, 256, 256)

        # save patch
        cv2.imwrite(patch_path, patch_img)
    
    label_file_all_lines.append(patch_path+' 1\n')
    label_file_occupied_lines.append(patch_path+' 1\n')
        
    cnt += 1
    #if cnt > 10:
    #    break


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


1861
1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060


3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699


5139
5140
5141
5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338


6780
6781
6782
6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977
6978
6979


In [35]:
set(label_file_all_lines)

{'/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied7059_DJI_0004_001.jpg 1\n',
 '/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied6853_VID_20220810_141753_00_001_2022-08-10_18-18-41_스크린샷.jpg 1\n',
 '/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied7281_DJI_0004_003.jpg 1\n',
 '/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied162_DJI_0012_001.jpg 1\n',
 '/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied392_DJI_0006_001.jpg 1\n',
 '/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied1242_DJI_0011_001.jpg 1\n',
 '/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied7355_DJI_0004_003.jpg 1\n',
 '/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied6529_DJI_0007_001.jpg 1\n',
 '/root/share/datasets/total_20220724_20220818_update_generated/Occupied/occupied3906_DJI_0

In [36]:
with open(DATASET_PATH + '/'+ dataset_name + '_all.txt','w') as label_file_all:
    for line in set(label_file_all_lines) :
        label_file_all.write(line)
    
with open(DATASET_PATH + '/' + dataset_name + '_occupied.txt','w') as label_file_occupied:   
    for line in set(label_file_occupied_lines) :
        label_file_occupied.write(line)

### Generate empty patches

In [39]:
cnt = 0
category = 'empty'
PATCH_PATH = EMPTY_PATH

# Open label txt file 
label_file_all_lines = list(open(DATASET_PATH + '/'+ dataset_name + '_all.txt', 'r').readlines()) if os.path.exists(DATASET_PATH + '/'+ dataset_name + '_all.txt') else []
label_file_empty_lines = list(open(DATASET_PATH + '/' + dataset_name + '_occupied.txt', 'r').readlines()) if os.path.exists(DATASET_PATH + '/'+ dataset_name + '_occupied.txt') else []
label_file_empty_type_lines = list(open(DATASET_PATH + '/' + dataset_name + '_empty_type.txt', 'r').readlines()) if os.path.exists(DATASET_PATH + '/'+ dataset_name + '_empty_type.txt') else []

for key in datasets[category].keys():
    print(key)
    dataset = datasets[category]
    data = dataset[key] # label src b1 b2 b3 b4
    bb_points = data['bb_points'] 
    poly_points = data['poly_points']
    
    img_path, label_img_path, patch_path, empty_type_img_path = define_img_path(dataset_name, data, key)
    
    # check existing file
    if os.path.exists(label_img_path):
        print('label image {} exists'.format(label_img_path.split('/')[-1]))
    if os.path.exists(patch_path):
        print('patch image {} exists'.format(patch_path.split('/')[-1]))
    if os.path.exists(empty_type_img_path):
        print('empty type image {} exists'.format(empty_type_img_path.split('/')[-1]))
        
    # label 이미지, patch, empty type 이미지가 없는 경우에만 생성
    if not os.path.exists(label_img_path) or not os.path.exists(patch_path) or not os.path.exists(empty_type_img_path): 
        # source image
        src = cv2.imread(img_path, cv2.IMREAD_COLOR)

        # labeled image
        if not os.path.exists(label_img_path):
            label_img = draw_label(img_path, bb_points)
            cv2.imwrite(label_img_path, label_img)

        # cropped patch
        if not os.path.exists(patch_path):
            patch_img = perspective_transform(src, bb_points, 256, 256)
            cv2.imwrite(patch_path, patch_img)
        
        # empty type image
        if not os.path.exists(empty_type_img_path): 
            empty_type_img = perspective_transform(src, poly_points, 256, 256)
            cv2.imwrite(empty_type_img_path, empty_type_img)
    
    label_file_all_lines.append(patch_path+' 0\n')
    label_file_empty_lines.append(patch_path+' 0\n')
    label_file_empty_type_lines.append(empty_type_img_path+' '+str(data['type'])+'\n')
        
    cnt += 1
    #if cnt > 10:
    #    break


1
label image empty1_VID_20220724_164941_00_017_2022-08-08_12-45-50_스크린샷_label.jpg exists
patch image empty1_VID_20220724_164941_00_017_2022-08-08_12-45-50_스크린샷.jpg exists
empty type image Empty_type_0_empty1_VID_20220724_164941_00_017_2022-08-08_12-45-50_스크린샷.jpg exists
2
label image empty2_VID_20220724_164941_00_017_2022-08-08_12-46-04_스크린샷_label.jpg exists
patch image empty2_VID_20220724_164941_00_017_2022-08-08_12-46-04_스크린샷.jpg exists
empty type image Empty_type_0_empty2_VID_20220724_164941_00_017_2022-08-08_12-46-04_스크린샷.jpg exists
3
label image empty3_VID_20220724_164941_00_017_2022-08-08_12-46-06_스크린샷_label.jpg exists
patch image empty3_VID_20220724_164941_00_017_2022-08-08_12-46-06_스크린샷.jpg exists
empty type image Empty_type_0_empty3_VID_20220724_164941_00_017_2022-08-08_12-46-06_스크린샷.jpg exists
4
label image empty4_VID_20220724_164941_00_017_2022-08-08_12-46-08_스크린샷_label.jpg exists
patch image empty4_VID_20220724_164941_00_017_2022-08-08_12-46-08_스크린샷.jpg exists
empty type i

1266
1267
1268
1269
1270
1271
1272
1273
1274
1275
1276
1277
1278
1279
1280
1281
1282
1283
1284
1285
1286
1287
1288
1289
1290
1291
1292
1293
1294
1295
1296
1297
1298
1299
1300
1301
1302
1303
1304
1305
1306
1307
1308
1309
1310
1311
1312
1313
1314
1315
1316
1317
1318
1319
1320
1321
1322
1323
1324
1325
1326
1327
1328
1329
1330
1331
1332
1333
1334
1335
1336
1337
1338
1339
1340
1341
1342
1343
1344
1345
1346
1347
1348
1349
1350
1351
1352
1353
1354
1355
1356
1357
1358
1359
1360
1361
1362
1363
1364
1365
1366
1367
1368
1369
1370
1371
1372
1373
1374
1375
1376
1377
1378
1379
1380
1381
1382
1383
1384
1385
1386
1387
1388
1389
1390
1391
1392
1393
1394
1395
1396
1397
1398
1399
1400
1401
1402
1403
1404
1405
1406
1407
1408
1409
1410
1411
1412
1413
1414
1415
1416
1417
1418
1419
1420
1421
1422
1423
1424
1425
1426
1427
1428
1429
1430
1431
1432
1433
1434
1435
1436
1437
1438
1439
1440
1441
1442
1443
1444
1445
1446
1447
1448
1449
1450
1451
1452
1453
1454
1455
1456
1457
1458
1459
1460
1461
1462
1463
1464
1465


2907
2908
2909
2910
2911
2912
2913
2914
2915
2916
2917
2918
2919
2920
2921
2922
2923
2924
2925
2926
2927
2928
2929
2930
2931
2932
2933
2934
2935
2936
2937
2938
2939
2940
2941
2942
2943
2944
2945
2946
2947
2948
2949
2950
2951
2952
2953
2954
2955
2956
2957
2958
2959
2960
2961
2962
2963
2964
2965
2966
2967
2968
2969
2970
2971
2972
2973
2974
2975
2976
2977
2978
2979
2980
2981
2982
2983
2984
2985
2986
2987
2988
2989
2990
2991
2992
2993
2994
2995
2996
2997
2998
2999
3000
3001
3002
3003
3004
3005
3006
3007
3008
3009
3010
3011
3012
3013
3014
3015
3016
3017
3018
3019
3020
3021
3022
3023
3024
3025
3026
3027
3028
3029
3030
3031
3032
3033
3034
3035
3036
3037
3038
3039
3040
3041
3042
3043
3044
3045
3046
3047
3048
3049
3050
3051
3052
3053
3054
3055
3056
3057
3058
3059
3060
3061
3062
3063
3064
3065
3066
3067
3068
3069
3070
3071
3072
3073
3074
3075
3076
3077
3078
3079
3080
3081
3082
3083
3084
3085
3086
3087
3088
3089
3090
3091
3092
3093
3094
3095
3096
3097
3098
3099
3100
3101
3102
3103
3104
3105
3106


4546
4547
4548
4549
4550
4551
4552
4553
4554
4555
4556
4557
4558
4559
4560
4561
4562
4563
4564
4565
4566
4567
4568
4569
4570
4571
4572
4573
4574
4575
4576
4577
4578
4579
4580
4581
4582
4583
4584
4585
4586
4587
4588
4589
4590
4591
4592
4593
4594
4595
4596
4597
4598
4599
4600
4601
4602
4603
4604
4605
4606
4607
4608
4609
4610
4611
4612
4613
4614
4615
4616
4617
4618
4619
4620
4621
4622
4623
4624
4625
4626
4627
4628


In [40]:
with open(DATASET_PATH + '/'+ dataset_name + '_all.txt','w') as label_file_all:
    for line in set(label_file_all_lines) :
        label_file_all.write(line)
    
with open(DATASET_PATH + '/' + dataset_name + '_empty.txt','w') as label_file_empty:   
    for line in set(label_file_empty_lines) :
        label_file_empty.write(line)

### Generate obstacle images

In [32]:
cnt = 0
category = 'obstacle'
PATCH_PATH = OBSTACLE_PATH

# Open label txt file 
label_file_obstacle_lines = list(open(DATASET_PATH + '/' + dataset_name + '_obstacle.txt', 'r').readlines()) if os.path.exists(DATASET_PATH + '/'+ dataset_name + '_obstacle.txt') else []

for key in datasets[category].keys():
    print(key)
    dataset = datasets[category]
    data = dataset[key] # label src b1 b2 b3 b4
    poly_points = data['poly_points']
    
    img_path, label_img_path, obstacle_img_path = define_img_path(dataset_name, data, key)
    
    # check existing file
    if os.path.exists(label_img_path):
        print('label image {} exists'.format(label_img_path.split('/')[-1]))
    if os.path.exists(obstacle_img_path):
        print('obstacle image {} exists'.format(obstacle_img_path.split('/')[-1]))
        
    # label 이미지, obstacle 이미지가 없는 경우에만 생성
    if not os.path.exists(label_img_path) or not os.path.exists(obstacle_img_path): 
        # source image
        src = cv2.imread(img_path, cv2.IMREAD_COLOR)

        # labeled image
        if not os.path.exists(label_img_path):
            label_img = draw_label(img_path, poly_points)
            cv2.imwrite(label_img_path, label_img)
        
        # empty type image
        if not os.path.exists(obstacle_img_path): 
            obstacle_img = perspective_transform(src, poly_points, 256, 256)
            cv2.imwrite(obstacle_img_path, obstacle_img)
    
    label_file_obstacle_lines.append(obstacle_img_path+' '+str(data['type'])+'\n')
        
    #cnt += 1
    #if cnt > 10:
    #    break


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [ ]:
set(label_file_obstacle_lines)

In [33]:
with open(DATASET_PATH + '/'+ dataset_name + '_obstacle.txt','w') as label_file_obstacle:
    for line in set(label_file_obstacle_lines) :
        label_file_obstacle.write(line)

In [15]:
import h5py

save_path = dataset_name+'.h5'
with h5py.File(save_path, 'w') as f:
    for key in datasets['occupied'].keys():
        print(key)
        dataset = datasets['occupied']
        data = dataset[key] # label src b1 b2 b3 b4
        label = data['label']
        src = data['src']
        print(src, label)
        bb_point = np.array([[data['b1'][0], data['b1'][1]],
                             [data['b2'][0], data['b2'][1]],
                             [data['b3'][0], data['b3'][1]],
                             [data['b4'][0], data['b4'][1]]], dtype=np.float32)
        # source image
        img_path = os.path.join(dataset_name, 'images', src)
        print('image size: %d bytes'%os.path.getsize(img_path))
        img_f = open(img_path, 'rb') 
        print(type(img_f)) 
        binary_data = img_f.read()      # read the image as python binary
        print(type(binary_data)) 
        #binary_data_np = np.asarray(binary_data)
        #dset = f.create_dataset(src+'_occupied_'+key, data=binary_data_np)  # write the data to hdf5 file
    f.close() 


1
VID_20220724_164941_00_017_2022-08-08_12-45-50_스크린샷.jpg 있음


KeyError: 'b1'

In [ ]:
print('hdf5 file size: %d bytes'%os.path.getsize(save_path))

In [ ]:
for key in datasets['empty'].keys():
    print(key)

In [ ]:
for key in datasets['obstacle'].keys():
    print(key)